Import mmsdk package:

In [1]:
from constants import SDK_PATH, DATA_PATH, WORD_EMB_PATH, CACHE_PATH
import sys

if SDK_PATH is None:
    print("SDK path is not specified! Please specify first in constants/paths.py")
    exit(0)
else:
    sys.path.append(SDK_PATH)

import mmsdk
import os
import re
import numpy as np
from mmsdk import mmdatasdk as md
from subprocess import check_call, CalledProcessError

# create folders for storing the data
if not os.path.exists(DATA_PATH):
    check_call(' '.join(['mkdir', '-p', DATA_PATH]), shell=True)

In [2]:
DATASET = md.cmu_mosei
all_num = DATASET.standard_folds.standard_train_fold + \
     DATASET.standard_folds.standard_test_fold + \
     DATASET.standard_folds.standard_valid_fold
print('all', len(all_num))
print('train', len(DATASET.standard_folds.standard_train_fold))
print('valid', len(DATASET.standard_folds.standard_valid_fold))
print('test', len(DATASET.standard_folds.standard_test_fold))


all 3227
train 2249
valid 300
test 678


Preparation import to modify mmsdk dataset alignment method

In [3]:
from mmsdk.mmdatasdk import log, computational_sequence
import numpy
import time
import struct
from tqdm import tqdm_notebook as tqdm

Inheritate from mmsdk with new methods: 

In [4]:

def save_htk_format(features, feature_type, folder, video_number):
    '''
    This function works for function align_upsampling_and_save. It save feature vectors of one video id into one 
    htk format file. 
    feature: feature of one video
    All files are of USER type.
    number of samples being consistent with number of samples in csd file
    sample bytes for COVAREP: 4 * 74 = 296
    sample period: 10 000.0 us (100000)
    paramkind: USER (9)
    '''
    #set default extension
    ext = '.txt'
    file_name = os.path.join(folder, feature_type, video_number)

    num_sample = len(features)
    byte_n_sample = num_sample.to_bytes(4, byteorder='big')

    period = 100000
    byte_period = period.to_bytes(4, byteorder = 'big')

    if feature_type == 'COVAREP':
        sample_b = 296
        ext = '.cov'
    elif feature_type == 'WordVec':
        sample_b = 1200
        ext = '.wvec'

    byte_sample_b = sample_b.to_bytes(2, byteorder = 'big')

    sample_type = 9
    byte_sample_type = sample_type.to_bytes(2, byteorder = 'big')
    header = byte_n_sample + byte_period + byte_sample_b + byte_sample_type

    output_byte = b''
    '''
    try:
        print(type(features))
        print(type(features[0]))
    except:
        print('features cannot be indexed')
        
    try:
        print(features[0].shape)
    except:
        print('features[0] is not np array')
    '''
    for datapoint in features:
        y = list(map(lambda x: struct.pack('>f', x), datapoint))
        byte_datapoint = b''.join(y)

        output_byte += byte_datapoint

    with open(file_name + ext, 'wb') as file:
        file.write(header + output_byte)



In [5]:

import pickle, os, json, codecs


def save_intervals(intervals, feature_type, folder, video_number):
    #set default extension
    ext = '.json'
    video_number = 'intervals_' + video_number
    file_name = os.path.join(folder, feature_type, video_number)
    
    if type(intervals) != list:
        intervals = intervals.tolist()
    json.dump(intervals, codecs.open(file_name + ext, 'w', encoding='utf-8'), indent=4)
    

In [6]:
class new_mmdataset(md.mmdataset):
    #TODO: Need tqdm bar for this as well
    def get_relevant_entries(self,reference):
        relevant_entries={}
        relevant_entries_np={}

        #pbar = tqdm(total=count,unit=" Computational Sequence Entries",leave=False)

        #otherseq_key: OpenFace, wordvec, etc
        for otherseq_key in set(list(self.computational_sequences.keys()))-set([reference]):
            relevant_entries[otherseq_key]={}
            relevant_entries_np[otherseq_key]={}
            sub_compseq=self.computational_sequences[otherseq_key]
            # for some_id in all video ids
            for key in list(sub_compseq.data.keys()):
                keystripped=key.split('[')[0]
                if keystripped not in relevant_entries[otherseq_key]:                           
                    relevant_entries[otherseq_key][keystripped]={}
                    relevant_entries[otherseq_key][keystripped]["intervals"]=[]                     
                    relevant_entries[otherseq_key][keystripped]["features"]=[]                                                            
                    
                relev_intervals=self.computational_sequences[otherseq_key].data[key]["intervals"]                                             
                relev_features=self.computational_sequences[otherseq_key].data[key]["features"]         
                if len(relev_intervals.shape)<2:
                    relev_intervals=relev_intervals[None,:]
                    relev_features=relev_features[None,:]

                relevant_entries[otherseq_key][keystripped]["intervals"].append(relev_intervals)
                relevant_entries[otherseq_key][keystripped]["features"].append(relev_features)
                
            for key in list(relevant_entries[otherseq_key].keys()):
                relev_intervals_np=numpy.concatenate(relevant_entries[otherseq_key][key]["intervals"],axis=0)                                 
                relev_features_np=numpy.concatenate(relevant_entries[otherseq_key][key]["features"],axis=0)
                sorted_indices=sorted(range(relev_intervals_np.shape[0]),key=lambda x: relev_intervals_np[x,0])                               
                relev_intervals_np=relev_intervals_np[sorted_indices,:]                         
                relev_features_np=relev_features_np[sorted_indices,:]

                relevant_entries_np[otherseq_key][key]={}
                relevant_entries_np[otherseq_key][key]["intervals"]=relev_intervals_np
                relevant_entries_np[otherseq_key][key]["features"]=relev_features_np
            log.status("Pre-alignment done for <%s> ..."%otherseq_key)
        return relevant_entries_np
    
    def intersect_and_copy_upsampling(self, ref_all, relevant_entry, not_enough_label, epsilon, log_file, feature_info):
        #ref_all: reference_entries[other_key][entry_key]['intervals'] e.g. [COVAREP][some video id]['intervals']
        #relevant_entry: relevant_entries[other_key][entry_key] e.g. [COVAREP][some video id]
        #epsilon: error allowed in alignment
        #ref_time < one interval in relevant_entry
        
        pbar_small=log.progress_bar(total=ref_all.shape[0],unit=" Segments",leave=False)
        pbar_small.set_description("Aligning: " + feature_info)
        
        sub=relevant_entry["intervals"]
        features=relevant_entry["features"]
        
        #finding where intersect happens
        pointer_b = 0 # for relevant_entry
        aligned_sub = []
        aligned_feature = []
        
        for i, inter in enumerate(ref_all):
            #print(pointer_b)
            if (abs(inter[0]-inter[1])<epsilon):
                pbar_small.update(1)
                continue
            pointer_c = pointer_b
            while(pointer_c < sub.shape[0]):
                if (inter[0] - sub[pointer_c][0]) > (-epsilon) and (sub[pointer_c][1] - inter[0]) > (-epsilon):
                    aligned_sub.append(sub[pointer_c])
                    aligned_feature.append(features[pointer_c])
                    break
                else:
                    pointer_c += 1
                
            if pointer_c == sub.shape[0]:
                diff = list(map(lambda x: abs(inter[0] - x), sub[:, 0]))
                min_diff = min(diff)
                pointer_c = diff.index(min_diff)
                with open(log_file, 'w+') as fi:
                    fi.write('no corresponding frame, find the closest one, {}, difference: {}\n'.format(feature_info, min_diff))
                aligned_sub.append(sub[pointer_c])
                aligned_feature.append(features[pointer_c])
            else:
                pointer_b = pointer_c

            pbar_small.update(1)
        
        aligned_sub = np.array(aligned_sub)
        aligned_feature = np.array(aligned_feature)
        zero_idx = np.where(np.isinf(aligned_feature))
        aligned_feature[zero_idx] = 0

        pbar_small.close()
        return aligned_sub,aligned_feature
    
    def align_upsampling_and_save(self, reference, id_idx, label_dataset, collapse_function=None, epsilon = 10e-6):
        folder = '/data/mifs_scratch/yw454/cmumosei_aligned'
        log_file = './mosei_alignment_log.txt'
        not_enough_label_file = './mosei_notenough_lable_videos.txt'
        no_valid_label_file = './mosei_no_lable_videos.txt'
        
        #aligned_output = {}
        count = 0
        
        ##self.computational_sequences.keys are COVERAP, OpenFace, WordVec, etc
        #for sequence_name in self.computational_sequences.keys():
        #    #init a dictionary to store different featues seperately
        #    aligned_output[sequence_name]={}
        
        if reference not in self.computational_sequences.keys():
            log.error("Computational sequence <%s> does not exist in dataset"%reference,error=True)
        
        #get data of reference feature
        refseq=self.computational_sequences[reference].data
        #unifying the dataset, removing any entries that are not in the reference computational sequence
        self.unify()
        
        #building the relevant entries to the reference - what we do in this section is simply removing all the [] from the entry ids and populating them into a new dictionary
        log.status("Pre-alignment based on <%s> computational sequence started ..."%reference)
        
        relevant_entries=self.get_relevant_entries(reference)
        log.status("Alignment starting ...")
        
        
        pbar = log.progress_bar(total=len(refseq.keys()),unit=" Computational Sequence Entries",leave=False)
        pbar.set_description("Overall Progress")
        # for some_id in all video ids
        for entry_key in list(refseq.keys()):
            not_enough_label = False
            if entry_key in id_idx:
                stored_idx = id_idx.index(entry_key)
                if stored_idx < 104 or (stored_idx > 104 and stored_idx < 1781):
                #if stored_idx != 1781:
                    continue
            
            label_len = label_dataset[entry_key]['intervals'][-1][1] - label_dataset[entry_key]['intervals'][0][0]
            reference_len = refseq[entry_key]['intervals'][-1][1] - refseq[entry_key]['intervals'][0][0]
            div = reference_len / label_len
            if div > 2:
                not_enough_label = True
                with open(not_enough_label_file, 'w+') as fw:
                    fw.write(entry_key + '\n')
            if label_len < 0:
                with open(no_valid_label_file, 'w+') as fw:
                    fw.write(entry_key + '\n')
                
            all_intersects = {}
            all_intersect_features = {}
            
            #for sequence_name in self.computational_sequences.keys():
            #    all_intersects[sequence_name] = []
            #    all_intersect_features[sequence_name] = []
            
            ref_all=refseq[entry_key]['intervals']
                
            #aligning all sequences to ref sequence (previous: align refer to refer as well, now: not include refer)
            #otherseq_key: other features; entry_key: some video id
                
            for otherseq_key in list(self.computational_sequences.keys()):
                if otherseq_key != reference:
                    feature_info = 'reference: {}, other feature {}, video id: {}'.format(reference, otherseq_key, entry_key)
                    intersects,intersects_features=self.intersect_and_copy_upsampling(ref_all,relevant_entries[otherseq_key][entry_key], not_enough_label, epsilon, log_file, feature_info)
                else:
                    intersects,intersects_features=refseq[entry_key]['intervals'][:,:],refseq[entry_key]['features'][:,:]
                    
                #print(type(intersects[0]))
                #print(type(intersects_features[0]))
                #print(len(intersects[0]))
                #print(len(intersects_features[0]))
                all_intersects[otherseq_key] = intersects
                all_intersect_features[otherseq_key] = intersects_features
                    

            #save features per video
            for sequence_name in self.computational_sequences.keys():
                video_code = id_idx.index(entry_key)
                video_code = str(video_code).zfill(6)
                
                save_htk_format(all_intersect_features[sequence_name], sequence_name, folder, video_code)
                save_intervals(all_intersects[sequence_name], sequence_name, folder, video_code)
                print('alignment saved for video {} feature {}.'.format(video_code, sequence_name))
            
            pbar.update(1)
        pbar.close()




In [7]:
# define your different modalities - refer to the filenames of the CSD files
basic_dict={'COVAREP': DATA_PATH + 'CMU_MOSEI_COVAREP.csd', 
            'WordVec': DATA_PATH + 'CMU_MOSEI_TimestampedWordVectors.csd'}
second_dict = {'Facet': DATA_PATH + 'CMU_MOSEI_VisualFacet42.csd',
            'OpenFace': DATA_PATH + 'CMU_MOSEI_VisualOpenFace2.csd'}
other_dict = {'Word': DATA_PATH + 'CMU_MOSEI_TimestampedWords.csd',
             'Phone': DATA_PATH + 'CMU_MOSEI_TimestampedPhones.csd'}
label_dict = {'mylabels':DATA_PATH + 'CMU_MOSEI_Labels.csd'}

In [8]:
# list the directory contents... let's see what features there are
data_files = os.listdir(DATA_PATH)
print('\n'.join(data_files))

CMU_MOSEI_VisualOpenFace2.csd
CMU_MOSEI_TimestampedWords.csd
CMU_MOSEI_COVAREP.csd
CMU_MOSEI_VisualFacet42.csd
CMU_MOSEI_TimestampedWordVectors.csd
CMU_MOSEI_TimestampedPhones.csd
CMU_MOSEI_Labels.csd
COVAREP.zip


In [9]:
basic_dataset = new_mmdataset(basic_dict)
second_dataset = new_mmdataset(second_dict)
label_dataset = new_mmdataset(label_dict)

validators eliminated
[2021-02-04 11:44:24.847] | Success | Computational sequence read from file /data/mifs_scratch/yw454/cmu_mosei_latest/CMU_MOSEI_COVAREP.csd ...
[2021-02-04 11:44:43.965] | Warning | Validation of the computational sequence skipped by user request.
validators eliminated
[2021-02-04 11:44:43.967] | Success | Computational sequence read from file /data/mifs_scratch/yw454/cmu_mosei_latest/CMU_MOSEI_TimestampedWordVectors.csd ...
[2021-02-04 11:44:58.940] | Warning | Validation of the computational sequence skipped by user request.
[2021-02-04 11:44:58.940] | Success | Dataset initialized successfully ... 
validators eliminated
[2021-02-04 11:44:58.956] | Success | Computational sequence read from file /data/mifs_scratch/yw454/cmu_mosei_latest/CMU_MOSEI_VisualFacet42.csd ...
[2021-02-04 11:45:17.242] | Warning | Validation of the computational sequence skipped by user request.
validators eliminated
[2021-02-04 11:45:17.255] | Success | Computational sequence read from 

In [10]:
[COVAREP, WordVec] = [basic_dataset.computational_sequences['COVAREP'],
                        basic_dataset.computational_sequences['WordVec']]
label = label_dataset.computational_sequences['mylabels']
OpenFace = second_dataset.computational_sequences['OpenFace']

In [11]:
count = 0
certain_frame = []
some_id = list(label.keys())
for i, video in enumerate(list(WordVec.keys())):
    feature = WordVec[video]['features'][:,:]
    interval = WordVec[video]['intervals'][:,:]
    zero_idx = []
    for j, f in enumerate(feature):
        if np.all((f == 0)):
            zero_idx.append(interval[j])
    '''
    if video in some_id:
        label_interval = label[video]['intervals'][:,:]
    '''
    if len(zero_idx) != 0:
        print(video, zero_idx)

print(count)
    
            

--qXJuDtHPw [array([0.01247166, 0.0723356 ]), array([1.57891156, 1.64875283]), array([2.40702948, 2.69637188]), array([5.05102041, 5.18072562]), array([5.59977324, 6.87687075]), array([7.16621315, 7.19614512]), array([7.64512472, 8.04421769]), array([8.81247166, 9.98979592]), array([11.31678005, 11.78571429]), array([13.51179138, 13.53174603]), array([14.59931973, 14.85873016]), array([15.35759637, 15.44739229]), array([15.9861678, 16.3553288]), array([17.27324263, 17.31315193]), array([18.6600907, 19.0292517]), array([19.82743764, 19.90725624]), array([21.24421769, 22.12222222]), array([22.99024943, 23.05011338]), array([23.47913832, 23.69863946]), array([28.03877551, 28.62743764]), array([29.82471655, 30.74263039]), array([35.03287982, 35.72131519]), array([36.89863946, 36.93854875]), array([37.77664399, 37.79659864]), array([39.83197279, 40.28095238]), array([43.03469388, 43.10453515]), array([43.43378685, 43.77301587]), array([44.75079365, 44.93038549]), array([45.77845805, 46.1077

-MeTTeMJBNc [array([0.01247166, 0.94036281]), array([4.36258503, 4.41247166]), array([6.43786848, 6.77709751]), array([8.71269841, 9.21156463]), array([ 9.95986395, 10.50861678]), array([12.69365079, 13.06281179]), array([15.17800454, 15.22789116]), array([16.75442177, 16.82426304]), array([18.67006803, 19.24875283]), array([20.49591837, 21.27414966]), array([26.27278912, 26.65192744]), array([27.72947846, 28.17845805]), array([29.09637188, 29.1861678 ]), array([30.45328798, 30.85238095]), array([31.65056689, 31.72040816]), array([33.08730159, 33.39659864]), array([38.67460317, 38.69455782]), array([39.74217687, 39.99160998]), array([41.75759637, 42.29637188]), array([42.7154195 , 42.76530612]), array([44.76077098, 45.09002268]), array([48.35260771, 48.62199546]), array([51.02653061, 51.40566893]), array([53.02199546, 53.37120181]), array([55.34671202, 55.52630385]), array([57.11269841, 57.51179138]), array([58.19024943, 58.22018141]), array([60.32539683, 60.55487528]), array([63.03922

-mqbVkbCndg [array([0.01247166, 0.06235828]), array([0.53129252, 0.76077098]), array([4.00340136, 4.56213152]), array([4.98117914, 5.31043084]), array([5.869161 , 6.4478458]), array([8.67278912, 9.21156463]), array([10.08956916, 10.16938776]), array([11.5861678 , 11.96530612]), array([12.80340136, 13.38208617]), array([13.75124717, 14.25011338]), array([15.2877551, 15.6968254]), array([16.3553288, 16.6446712]), array([16.87414966, 16.98390023]), array([19.15895692, 19.62789116]), array([23.34943311, 24.19750567]), array([25.70408163, 25.79387755]), array([27.5399093, 27.8292517]), array([29.37573696, 29.61519274]), array([31.07188209, 31.2414966 ]), array([32.02970522, 32.30907029]), array([32.81791383, 32.87777778]), array([33.5861678 , 33.63605442]), array([34.19478458, 34.83333333]), array([36.14036281, 36.669161  ]), array([36.92857143, 37.05827664]), array([39.88185941, 40.0814059 ]), array([41.01927438, 41.49818594]), array([42.12675737, 42.29637188]), array([43.02471655, 43.6034

0FA32bEZ6xI [array([0.01247166, 5.79931973]), array([7.50544218, 7.56530612]), array([8.40340136, 8.88231293]), array([ 9.6106576 , 10.77800454]), array([13.75124717, 14.3399093 ]), array([16.13582766, 16.22562358]), array([17.89183673, 17.92176871]), array([18.84965986, 19.91723356]), array([21.15442177, 21.19433107]), array([22.38163265, 22.43151927]), array([23.31950113, 23.80839002]), array([26.28276644, 26.44240363]), array([27.14081633, 27.22063492]), array([28.25827664, 29.66507937]), array([34.23469388, 34.5739229 ]), array([36.12040816, 36.42970522]), array([36.94852608, 37.27777778]), array([37.77664399, 38.05600907]), array([38.69455782, 39.88185941]), array([41.99705215, 42.18662132]), array([43.1244898 , 43.18435374]), array([43.39387755, 43.4138322 ]), array([43.72312925, 45.16984127]), array([47.51451247, 47.54444444]), array([48.26281179, 48.50226757]), array([49.45011338, 50.30816327]), array([52.31360544, 52.34353742]), array([55.28684807, 55.71587302]), array([59.846

0p9XKC_J3hU [array([2.61655329, 2.88594104]), array([9.45102041, 9.81020408]), array([10.68820862, 10.77800454]), array([15.17800454, 15.54716553]), array([18.24104308, 18.34081633]), array([19.438322  , 19.50816327]), array([22.23197279, 23.00022676]), array([28.92675737, 29.10634921]), array([30.8723356, 31.161678 ]), array([33.59614512, 33.93537415]), array([35.81111111, 36.07052154]), array([38.53492063, 38.76439909]), array([40.81972789, 40.9893424 ]), array([43.14444444, 43.19433107]), array([44.56122449, 45.70861678])]
0r8KVXUCV6c [array([0.01247166, 0.97029478]), array([5.41020408, 6.46780045]), array([8.37346939, 8.46326531]), array([10.08956916, 11.17709751]), array([13.33219955, 13.55170068]), array([14.9585034 , 14.98843537]), array([15.54716553, 15.92630385]), array([16.38526077, 16.44512472]), array([17.42290249, 17.50272109]), array([19.19886621, 19.22879819]), array([20.21655329, 20.63560091]), array([21.18435374, 21.25419501]), array([22.28185941, 22.8106576 ]), array(

...

xnNZyfhusAk [array([1.40929705, 1.49909297]), array([3.56439909, 3.69410431]), array([4.5521542 , 4.94126984]), array([8.73265306, 9.27142857]), array([10.23922902, 10.42879819]), array([12.01519274, 12.6537415 ]), array([14.94852608, 15.11814059]), array([15.89637188, 16.3553288 ]), array([16.98390023, 17.14353742]), array([17.91179138, 18.24104308]), array([18.99931973, 19.0292517 ]), array([19.87732426, 19.89727891]), array([20.46598639, 20.56575964]), array([22.18208617, 23.11995465]), array([25.22517007, 25.56439909]), array([26.4324263, 26.5122449]), array([27.48004535, 27.91904762]), array([30.9122449 , 32.01972789]), array([34.16485261, 34.63378685]), array([36.09047619, 36.48956916]), array([38.34535147, 38.81428571]), array([41.61791383, 41.82743764]), array([44.12222222, 44.67097506]), array([45.97800454, 46.03786848]), array([48.63197279, 48.72176871]), array([49.40022676, 49.43015873]), array([51.26598639, 51.5553288 ]), array([52.38344671, 52.43333333]), array([53.8301587

yHtR71rx16I [array([1.97800454, 2.10770975]), array([3.75396825, 3.86371882]), array([4.94126984, 5.34036281]), array([7.09637188, 7.20612245]), array([10.42879819, 10.79795918]), array([12.92312925, 13.2324263 ]), array([13.66145125, 13.71133787]), array([14.43968254, 14.47959184]), array([15.16802721, 15.20793651]), array([16.94399093, 17.12358277]), array([17.40294785, 18.0414966 ]), array([18.49047619, 19.24875283]), array([21.91269841, 22.55124717]), array([23.00022676, 23.25963719]), array([24.65646258, 24.69637188]), array([25.74399093, 25.76394558]), array([25.97346939, 26.38253968]), array([27.33038549, 27.7893424 ]), array([29.8845805 , 30.37346939]), array([31.00204082, 31.05192744]), array([32.04965986, 32.269161  ]), array([33.13718821, 33.35668934]), array([33.81564626, 33.90544218]), array([34.26462585, 34.34444444]), array([36.94852608, 36.96848073]), array([37.3276644 , 37.35759637]), array([38.69455782, 38.77437642]), array([39.6324263 , 39.90181406]), array([41.15895

ygb8Cfxghbs [array([0.01247166, 2.42698413]), array([4.06326531, 4.08321995]), array([4.82154195, 5.59977324]), array([9.06190476, 9.38117914]), array([10.53854875, 10.60839002]), array([10.79795918, 11.04739229]), array([11.9952381 , 12.52403628]), array([15.9462585 , 16.47505669]), array([16.81428571, 17.36303855]), array([19.49818594, 19.79750567]), array([20.47596372, 20.49591837]), array([20.90498866, 20.98480726]), array([21.15442177, 21.22426304]), array([22.76077098, 23.64875283]), array([26.71179138, 26.75170068]), array([27.55986395, 27.62970522]), array([29.13628118, 29.72494331]), array([33.14716553, 33.17709751]), array([35.14263039, 35.40204082]), array([37.01836735, 38.61473923]), array([41.69773243, 41.92721088]), array([44.78072562, 45.41927438]), array([46.55668934, 46.58662132]), array([48.48231293, 48.59206349]), array([48.81156463, 49.05102041]), array([51.87460317, 52.1739229 ]), array([54.14943311, 55.27687075]), array([58.12040816, 58.19024943]), array([59.62698

zJWmmDk9fCE [array([0.01247166, 0.53129252]), array([3.36485261, 3.65419501]), array([6.35804989, 6.39795918]), array([7.02653061, 7.61519274]), array([12.41428571, 12.71360544]), array([15.12811791, 15.41746032]), array([21.02471655, 21.3739229 ]), array([23.7185941, 24.0877551]), array([28.33809524, 28.63741497]), array([33.41655329, 33.90544218]), array([35.66145125, 35.98072562]), array([37.6968254 , 38.34535147]), array([41.95714286, 42.52585034]), array([44.01247166, 44.30181406]), array([48.85147392, 49.25056689]), array([51.8446712 , 52.22380952]), array([53.2414966 , 53.60068027]), array([56.27460317, 56.29455782]), array([59.67687075, 60.00612245]), array([61.21337868, 61.48276644]), array([62.81972789, 63.28866213]), array([66.33174603, 66.38163265]), array([66.70090703, 67.1       ]), array([69.29501134, 69.97346939]), array([73.5952381 , 73.72494331]), array([75.37120181, 75.75034014]), array([78.95306122, 79.18253968]), array([80.69909297, 81.00839002]), array([82.8442176

zjYEBwXGD8I [array([0.01247166, 0.89047619]), array([3.1553288 , 3.22517007]), array([6.74716553, 7.37573696]), array([9.41111111, 9.44104308]), array([10.5585034 , 10.87777778]), array([14.55941043, 14.63922902]), array([15.47732426, 15.72675737]), array([20.45600907, 20.49591837]), array([20.72539683, 21.24421769]), array([24.52675737, 24.72630385]), array([25.7739229 , 26.04331066]), array([27.84920635, 28.73718821]), array([28.90680272, 28.94671202]), array([31.13174603, 31.2814059 ]), array([35.9707483 , 36.38979592]), array([37.72675737, 37.87641723]), array([39.23333333, 39.65238095]), array([42.60566893, 42.85510204]), array([43.76303855, 43.82290249]), array([45.04013605, 45.41927438]), array([49.77936508, 50.06870748]), array([51.8845805 , 52.10408163]), array([53.56077098, 53.94988662]), array([54.08956916, 54.35895692]), array([55.69591837, 55.83560091]), array([59.83650794, 60.08594104]), array([62.38072562, 62.71995465]), array([63.57800454, 63.73764172]), array([64.83514

In [23]:
some_id = list(label.keys())[1]
if some_id in all_num:
    print(label[some_id]['intervals'][:, :])

[[ 82.753 100.555]
 [119.919 125.299]
 [  4.84   14.052]
 [ 13.211  27.521]
 [ 26.541  41.3  ]
 [ 74.083  82.776]]


In [13]:
utterance = 0
yesterday = 0
for i, video in enumerate(list(WordVec.keys())):
    utterance += WordVec[video]['intervals'].shape[0]
    if i > 2132 and i <= 2270: # and i >= 780: 
        yesterday += WordVec[video]['intervals'].shape[0]
            
print(yesterday / utterance)

0.03206996277692446


In [12]:
'''
weird_acoustic = []
norm_acoustic = []
for i, k in enumerate(list(COVAREP.keys())):
    interval = COVAREP[k]['intervals']
    end_frame = int((interval[-1][0] - interval[0][0]) * 100)
    if abs(end_frame - (len(interval) - 1)) > 3:
        weird_acoustic.append(k)
        #print(end_frame, (len(interval) - 1))
    else:
        norm_acoustic.append(k)
    if i == 0:
        print(interval[:, :])
        
      
print(len(weird_acoustic))
#print(len(norm_acoustic))
if len(weird_acoustic) > 2:
    for i in range(2):
        interval = COVAREP[weird_acoustic[i]]['intervals'][:, :]

        for j in range(len(interval) - 1):

            if abs(interval[j][1] - interval[j+1][0]) > 1e-6:
                print(j, interval[j][1], interval[j+1][0])
            

            if abs(interval[j][1] - interval[j][0] - 0.01) >  1e-6:
                print(j, interval[j][1], interval[j][0])
            

        print(COVAREP[weird_acoustic[i]]['intervals'][-1])
        print(COVAREP[weird_acoustic[i]]['intervals'][0])

        print(int((interval[-1][0] - interval[0][0]) * 100))
        print(len(COVAREP[weird_acoustic[i]]['intervals']) - 1)

'''    
    

"\nweird_acoustic = []\nnorm_acoustic = []\nfor i, k in enumerate(list(COVAREP.keys())):\n    interval = COVAREP[k]['intervals']\n    end_frame = int((interval[-1][0] - interval[0][0]) * 100)\n    if abs(end_frame - (len(interval) - 1)) > 3:\n        weird_acoustic.append(k)\n        #print(end_frame, (len(interval) - 1))\n    else:\n        norm_acoustic.append(k)\n    if i == 0:\n        print(interval[:, :])\n        \n      \nprint(len(weird_acoustic))\n#print(len(norm_acoustic))\nif len(weird_acoustic) > 2:\n    for i in range(2):\n        interval = COVAREP[weird_acoustic[i]]['intervals'][:, :]\n\n        for j in range(len(interval) - 1):\n\n            if abs(interval[j][1] - interval[j+1][0]) > 1e-6:\n                print(j, interval[j][1], interval[j+1][0])\n            \n\n            if abs(interval[j][1] - interval[j][0] - 0.01) >  1e-6:\n                print(j, interval[j][1], interval[j][0])\n            \n\n        print(COVAREP[weird_acoustic[i]]['intervals'][-1])\n 

In [16]:
wordvec_with_gap = {}
not_zeros_start = set()
#video = list(WordVec.keys())[0]
for k in list(WordVec.keys()):
    interval = WordVec[k]['intervals']
    #if k == video:
    #    print(interval[:, :])
    if int(np.floor(interval[0][0])) != 0:
        not_zeros_start.add(k)
        print(interval[0][0])
    for i in range(interval.shape[0] - 1):
        #if k == video:
        #    print(interval[i+1][0], interval[i][1])
        if abs(interval[i + 1][0] - interval[i][1]) > 1e-3:
            if k in wordvec_with_gap:
                wordvec_with_gap[k] += 1
            else:
                wordvec_with_gap[k] = 1

print(wordvec_with_gap)
print(len(not_zeros_start))

{}
0


In [14]:
not_enough_word = set()
not_enough_label = set()
error_video = set()
no_labels = set()
label_keys = set(label.keys())
long_video_file = './video_short_label.txt'

for k in list(COVAREP.keys()):
    acoustic = COVAREP[k]['intervals'][-1][1]
    language = WordVec[k]['intervals'][-1][1]
    
    if language / acoustic > 2 or acoustic / language > 2 or language / acoustic < 0:
        not_enough_word.add(k)
    
    if k in label_keys:
        annotations = label[k]['intervals'][-1][1] - label[k]['intervals'][0][0]
        
        if annotations < 0: # annotations / acoustic > 2 or acoustic / annotations > 2 or 
        #if annotations - language > 1:
            if k in all_num:
                not_enough_label.add(k)
                #print(COVAREP[k]['intervals'][0][0], label[k]['intervals'][0][0])
                #print(acoustic, annotations)
                #print(k)
                #print('acoustic:', COVAREP[k]['intervals'][-1][-1], 'label', label[k]['intervals'][-1][-1])
            else:
                error_video.add(k)
                
                #with open(long_video_file, 'w+') as f_w:
                #    f_w.write(k + '\n')
            
    else:
        no_labels.add(k)
'''
print('========================================') 
print(len(not_enough_label))
print(len(not_enough_word))
print(len(error_video))

print(len((not_enough_label & not_enough_word)))

print(len(no_labels))  
print(len(no_labels & set(all_num)))
print(len((label_keys - not_enough_label) & not_enough_word))
'''   

for i, video in enumerate(not_enough_label):
    if i < 2:
        print(video)
        print('COVAREP last interval', COVAREP[video]['intervals'][-1][1])
        print('WordVec last interval', WordVec[video]['intervals'][-1][1])
        print(label[video]['intervals'][-1][1])
        print(label[video]['intervals'][:, :])
        #annotations = label[video]['intervals'][-1][1] - label[k]['intervals'][0][0]
        #acoustic = COVAREP[video]['intervals'][-1][1]
        #print(acoustic / annotations)

        
     


ZDz8Qr-sJ3E
COVAREP last interval 119.35000000000001
WordVec last interval 119.321315193
73.217
[[80.728 90.987]
 [14.159 23.041]
 [22.041 26.483]
 [67.638 73.217]]
trQLgl6ncmk
COVAREP last interval 98.17
WordVec last interval 98.1394558821
59.818
[[74.881 80.66 ]
 [79.66  96.564]
 [13.98  20.128]
 [31.25  44.912]
 [53.709 59.818]]


In [21]:
video = 'c7xUcM68IFE'
print(video in list(COVAREP.keys()))
print(video in label_keys)
annotations = label[k]['intervals'][-1][1] - label[k]['intervals'][0][0]
acoustic = COVAREP[k]['intervals'][-1][1]
print(annotations / acoustic > 2)
print(acoustic / annotations > 2)
print(annotations / acoustic > 2 or acoustic / annotations > 2)

True
True
False
True
True


In [23]:
video = '-NFrJFQijFE'
print(label[video]['intervals'][:10])
print(COVAREP[video]['intervals'][-1][1], COVAREP[video]['intervals'][0][0])
print(OpenFace[video]['intervals'][-1][1], OpenFace[video]['intervals'][0][0])

[[-0.47755102  4.10430839]
 [ 3.37369615  9.02312925]
 [ 8.02312925 14.72018141]
 [44.11111111 54.769161  ]]
570.0 0.0
569.92 0.0


In [44]:
video_id_record = os.path.join('/data/mifs_scratch/yw454/cmumosei_aligned', 'video_id.json')

with open(video_id_record, 'r') as json_file:
    video_ids = json.load(json_file)

basic_dataset.align_upsampling_and_save('COVAREP', video_ids)



[2021-01-24 02:53:58.267] | Status  | Unify was called ...
[2021-01-24 02:53:58.277] | Warning | PEBwwe0PLZ8 entry is not shared among all sequences, removing it ...
[2021-01-24 02:53:58.280] | Success | Unify completed ...
[2021-01-24 02:53:58.280] | Status  | Pre-alignment based on <COVAREP> computational sequence started ...










  0%|          | 0/3836 [00:00<?, ? Computational Sequence Entries/s]







Overall Progress:   0%|          | 0/3836 [00:00<?, ? Computational Sequence Entries/s]








  0%|          | 0/5459 [00:00<?, ? Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:   0%|          | 0/5459 [00:00<?, ? Segments/s]

[2021-01-24 02:54:19.297] | Status  | Pre-alignment done for <WordVec> ...
[2021-01-24 02:54:20.331] | Status  | Alignment starting ...
(5459, 2)
(5459, 74)











Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:   9%|▉         | 513/5459 [00:00<00:00, 5128.32 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  22%|██▏       | 1212/5459 [00:00<00:00, 5572.12 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  35%|███▌      | 1926/5459 [00:00<00:00, 5965.00 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  48%|████▊     | 2647/5459 [00:00<00:00, 6289.07 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  62%|██████▏   | 3361/5459 [00:00<00:00, 6520.21 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  75%|███████▍  | 4084/5459 [00:00<00:00, 6717.07 Segments/s]








Aligning: reference: COVAREP, other feature WordVec, video id: HUOMbK1x7MI:  88%|████████▊ | 4807/5459 [00:00<00:00, 6861.

COVAREP
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
(74,)
alignment saved for video 001815.
WordVec
<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
(300,)










Overall Progress:   0%|          | 1/3836 [00:06<6:51:32,  6.44s/ Computational Sequence Entries]







                                                                                                 

alignment saved for video 001815.


In [47]:
print(COVAREP['HUOMbK1x7MI']['features'].shape)

(5459, 74)
